## Flexible Design for Funding Public Goods

In [1]:
import numpy as np

# Number of Citizens in the Society
N = 30

# Society is a set of citizens
society = set(range(N))

# Community is a random subset of the society. The community size is from 1 up to 1/2 of the society.
community = np.random.choice(a=list(society), size=np.random.randint(1, len(society)/2), replace=False, p=None)

# Public Goods are proposed by community members. Cardinality is from 1 up to 1/2 size of the community.
public_goods = list(enumerate(np.random.choice(a=list(community), size=np.random.randint(1, len(community)/2), replace=True, p=None)))

## 3.1 Side Quest: Generating Value Functions

### Polynomial Generator.

In [2]:
c1 = {'exponent': 1,
 'f0': 0.2,
 'f1': 0.8,
 'initial_slope': 1,
 'name': 'CurveGenerator18499',
 'num_oscillations': 2}

In [3]:
import param
import numpy as np
import pandas as pd
import hvplot.pandas
import panel as pn

class CurveGenerator(param.Parameterized):
    f0 = param.Number(default=0.2, bounds=(0, 1), doc="Value of f(0)")
    f1 = param.Number(default=0.8, bounds=(0, 1), doc="Value of f(1)")
    initial_slope = param.Number(default=1, bounds=(-5, 5), doc="Initial slope of the curve")
    exponent = param.Number(default=1, bounds=(1, 5), doc="Exponent of the curve")
    num_oscillations = param.Integer(default=1, bounds=(0, 5), doc="Number of oscillations/peaks in the curve")
    
    @param.depends('f0', 'f1', 'initial_slope', 'exponent', 'num_oscillations')
    def curve(self, x):
        epsilon = 1e-10
        b = self.f0
        a = self.initial_slope / (self.exponent * (b + epsilon)**(self.exponent-1))
        c = (self.f1 - self.f0 - a) / 2
        d = self.num_oscillations
        y = a*x**self.exponent + b + c*np.sin(d*np.pi*x)
        
        # Scale and shift the curve to ensure it starts at f0 and ends at f1
        y = self.f0 + (self.f1 - self.f0) * (y - y.min()) / (y.max() - y.min())
        
        return y
    
    @param.depends('f0', 'f1', 'initial_slope', 'exponent', 'num_oscillations')
    def view(self):
        x = np.linspace(0, 1, 100)
        y = self.curve(x)
        df = pd.DataFrame({'x': x, 'y': y})
        return df.hvplot.line(x='x', y='y', ylim=(0, 1.01))

curve_gen = CurveGenerator(**c1)
pn.Row(curve_gen.param, curve_gen.view).servable()


Row
    [0] Column(margin=(5, 10), name='CurveGenerator')
        [0] StaticText(value='<b>CurveGenerator</b>')
        [1] FloatSlider(name='F0', value=0.2)
        [2] FloatSlider(name='F1', value=0.8)
        [3] FloatSlider(end=5, name='Initial slope', start=-5, value=1)
        [4] FloatSlider(end=5, name='Exponent', start=1, value=1)
        [5] IntSlider(end=5, name='Num oscillations', value=2)
    [1] ParamMethod(method, _pane=HoloViews, defer_load=False)

In [4]:
curve_gen.param.values()

{'exponent': 1,
 'f0': 0.2,
 'f1': 0.8,
 'initial_slope': 1,
 'name': 'CurveGenerator18499',
 'num_oscillations': 2}

### Sigmoid Generator

In [5]:
s1 = {'exponent': 0.3,
 'f0': 0,
 'f1': 0.5,
 'initial_slope': -5,
 'name': 'SigmoidGenerator03300',
 'oscillations': 2}

s2 = {'exponent': 0.4,
 'f0': 0,
 'f1': 0.5,
 'initial_slope': 4.4,
 'name': 'SigmoidGenerator03300',
 'oscillations': 2}

In [6]:
import numpy as np
import pandas as pd
import panel as pn
import param
import hvplot.pandas

class SigmoidGenerator(param.Parameterized):
    f0 = param.Number(default=0.5, bounds=(0, 1), doc="Value of the function at x=0")
    f1 = param.Number(default=0.5, bounds=(0, 1), doc="Value of the function at x=1")
    initial_slope = param.Number(default=1, bounds=(-5, 5), doc="Initial slope of the curve")
    exponent = param.Number(default=0.3, bounds=(0.1, 0.5), doc="Exponent of the curve")
    oscillations = param.Integer(default=1, bounds=(1, 5), doc="Number of oscillations/peaks in the curve")
    
    @param.depends('f0', 'f1', 'initial_slope', 'exponent', 'oscillations')
    def view(self):
        x = np.linspace(0, 1, 400)
        y = self.f0 + (self.f1 - self.f0) / (1 + np.exp(-self.initial_slope * (x - 0.5) * 10))**self.exponent
        y = y + 0.1 * np.sin(self.oscillations * np.pi * x)
        
        # Clip y values to ensure they stay within [0, 1]
        y = np.clip(y, 0, 1)
        
        df = pd.DataFrame({'x': x, 'y': y})
        return df.hvplot.line(x='x', y='y', ylim=(-0.01, 1.01))

sigmoid_gen = SigmoidGenerator(**s2)
pn.Row(sigmoid_gen.param, sigmoid_gen.view).servable()


Row
    [0] Column(margin=(5, 10), name='SigmoidGenerator')
        [0] StaticText(value='<b>SigmoidGenerator</b>')
        [1] FloatSlider(name='F0')
        [2] FloatSlider(name='F1', value=0.5)
        [3] FloatSlider(end=5, name='Initial slope', start=-5, value=4.4)
        [4] FloatSlider(end=0.5, name='Exponent', start=0.1, value=0.4)
        [5] IntSlider(end=5, name='Oscillations', start=1, value=2)
    [1] ParamMethod(method, _pane=HoloViews, defer_load=False)

In [7]:
sigmoid_gen.param.values()

{'exponent': 0.4,
 'f0': 0,
 'f1': 0.5,
 'initial_slope': 4.4,
 'name': 'SigmoidGenerator03300',
 'oscillations': 2}

In [8]:
p1 = {'exponent_param': 0.2,
 'f0': 0.1,
 'f1': 0.8,
 'name': 'PowerFunctionGenerator22564'}

### Power Function Generator

In [9]:
import numpy as np
import pandas as pd
import panel as pn
import param
import hvplot.pandas

class PowerFunctionGenerator(param.Parameterized):
    f0 = param.Number(default=0.1, bounds=(0, 1), doc="Value of the function at x=0")
    f1 = param.Number(default=0.5, bounds=(0, 1), doc="Value of the function at x=1")
    exponent_param = param.Number(default=0.5, bounds=(0.1, 2), doc="Parameter determining the exponent and slope")
    
    @param.depends('f0', 'f1', 'exponent_param')
    def view(self):
        epsilon = 1e-10

        x = np.linspace(0.001, 1, 400)  # Start from 0.001 to avoid division by zero
        
        # Calculate the exponent based on the provided parameter
        b = 2 * self.exponent_param  # This maps [0, 1] to [0, 2] for the exponent
        
        # Using the conditions f(0) = f0 and f(1) = f1 to solve for 'a' and 'c'
        a = self.f0
        c = (self.f1 - self.f0) / (1 ** b - 0 ** b + epsilon)
        
        y = a + c * x ** b
        
        # Clip y values to ensure they stay within [0, 1]
        y = np.clip(y, 0, 1)
        
        df = pd.DataFrame({'x': x, 'y': y})
        return df.hvplot.line(x='x', y='y', ylim=(0, 1.01))

power_func_gen = PowerFunctionGenerator(**p1)
pn.Row(power_func_gen.param, power_func_gen.view).servable()


Row
    [0] Column(margin=(5, 10), name='PowerFunctionGenerator')
        [0] StaticText(value='<b>PowerFunctionGenerator...)
        [1] FloatSlider(name='F0', value=0.1)
        [2] FloatSlider(name='F1', value=0.8)
        [3] FloatSlider(end=2, name='Exponent param', start=0.1, value=0.2)
    [1] ParamMethod(method, _pane=HoloViews, defer_load=False)

In [10]:
power_func_gen.param.values()

{'exponent_param': 0.2,
 'f0': 0.1,
 'f1': 0.8,
 'name': 'PowerFunctionGenerator22564'}

### Generating the Generators with NumberGen and Param.

In [11]:
import numbergen as ng

# For CurveGenerator
polynomial_curve_generator_params = dict(
    f0=ng.UniformRandom(lbound=0, ubound=1)(),
    f1=ng.UniformRandom(lbound=0, ubound=1)(),
    initial_slope=ng.UniformRandom(lbound=-5, ubound=5)(),
    exponent=ng.UniformRandom(lbound=1, ubound=5)(),
    num_oscillations=int(ng.UniformRandom(lbound=0, ubound=5)())
)

# For SigmoidGenerator
sigmoid_curve_generator_params = dict(
    f0=ng.UniformRandom(lbound=0, ubound=1)(),
    f1=ng.UniformRandom(lbound=0, ubound=1)(),
    initial_slope=ng.UniformRandom(lbound=-5, ubound=5)(),
    exponent=ng.UniformRandom(lbound=0.1, ubound=0.5)(),
    oscillations=int(ng.UniformRandom(lbound=1, ubound=5)())
)

# For PowerFunctionGenerator
power_curve_generator_params = dict(
    f0=ng.UniformRandom(lbound=0, ubound=0.5)(),
    f1=ng.UniformRandom(lbound=0, ubound=1)(),
    exponent_param=ng.UniformRandom(lbound=0.1, ubound=2)()
)

# Now, you can use these dictionaries to create instances of your classes as you've done in your code.


### Polynomial Value Function Generator

In [12]:
# Instantiate CurveGenerator with polynomial_curve_generator_params
polynomial_curve_gen_instance = CurveGenerator(**polynomial_curve_generator_params)

polynomial_curve_gen_instance.view()


:Curve   [x]   (y)

### Sigmoid Vlue Function Generator

In [13]:
# Instantiate SigmoidGenerator with sigmoid_curve_generator_params
sigmoid_curve_gen_instance = SigmoidGenerator(**sigmoid_curve_generator_params)
sigmoid_curve_gen_instance.view()

:Curve   [x]   (y)

### Power Function Value Function Generator

In [14]:
# Instantiate PowerFunctionGenerator with power_curve_generator_params
power_curve_gen_instance = PowerFunctionGenerator(**power_curve_generator_params)
power_curve_gen_instance.view()

:Curve   [x]   (y)

In [15]:
value_generators = [
    (CurveGenerator, polynomial_curve_generator_params),
    (SigmoidGenerator, sigmoid_curve_generator_params),
    (PowerFunctionGenerator, power_curve_generator_params),
]

# Generate a random index
index = np.random.choice(len(value_generators))

# Use the index to select an item from value_generators
selected_generator = value_generators[index]

In [16]:
index

0

In [17]:
selected_generator

(__main__.CurveGenerator,
 {'f0': 0.7461067908452278,
  'f1': 0.8220753228947874,
  'initial_slope': -3.909650465504173,
  'exponent': 4.470900164637493,
  'num_oscillations': 2})

In [18]:
selected_generator[0]

__main__.CurveGenerator

In [19]:
selected_generator[0](**selected_generator[1])

CurveGenerator(exponent=4.470900164637493, f0=0.7461067908452278, f1=0.8220753228947874, initial_slope=-3.909650465504173, name='CurveGenerator01692', num_oscillations=2)

In [20]:
import numbergen as ng
import numpy as np


# For CurveGenerator
polynomial_curve_generator_params = dict(
    f0=ng.UniformRandom(lbound=0, ubound=1)(),
    f1=ng.UniformRandom(lbound=0, ubound=1)(),
    initial_slope=ng.UniformRandom(lbound=-5, ubound=5)(),
    exponent=ng.UniformRandom(lbound=1, ubound=5)(),
    num_oscillations=int(ng.UniformRandom(lbound=0, ubound=5)())
)

# For SigmoidGenerator
sigmoid_curve_generator_params = dict(
    f0=ng.UniformRandom(lbound=0, ubound=1)(),
    f1=ng.UniformRandom(lbound=0, ubound=1)(),
    initial_slope=ng.UniformRandom(lbound=-5, ubound=5)(),
    exponent=ng.UniformRandom(lbound=0.1, ubound=0.5)(),
    oscillations=int(ng.UniformRandom(lbound=1, ubound=5)())
)

# For PowerFunctionGenerator
power_curve_generator_params = dict(
    f0=ng.UniformRandom(lbound=0, ubound=1)(),
    f1=ng.UniformRandom(lbound=0, ubound=1)(),
    exponent_param=ng.UniformRandom(lbound=0.1, ubound=2)()
)

# Now, you can use these dictionaries to create instances of your classes as you've done in your code.
value_generators = np.array([
    (CurveGenerator, polynomial_curve_generator_params),
    (SigmoidGenerator, sigmoid_curve_generator_params),
    (PowerFunctionGenerator, power_curve_generator_params),
])

# Generate a random array of indices of length n
samples = np.random.choice(len(value_generators), size=len(public_goods)*len(society))

# Use numpy's advanced indexing to obtain the selected_generators
sampled_generators = value_generators[samples]

# Instantiate utility curves using python param and numbergen
sampled_utility = [Generator(**params) for Generator, params in sampled_generators]

sampled_utility[:5]



[SigmoidGenerator(exponent=0.14660983723236845, f0=0.054406961802819676, f1=0.7076339103787128, initial_slope=4.662798898558647, name='SigmoidGenerator01706', oscillations=3),
 SigmoidGenerator(exponent=0.14660983723236845, f0=0.054406961802819676, f1=0.7076339103787128, initial_slope=4.662798898558647, name='SigmoidGenerator01707', oscillations=3),
 PowerFunctionGenerator(exponent_param=0.625487175284582, f0=0.622817884800272, f1=0.6687864412671407, name='PowerFunctionGenerator01708'),
 SigmoidGenerator(exponent=0.14660983723236845, f0=0.054406961802819676, f1=0.7076339103787128, initial_slope=4.662798898558647, name='SigmoidGenerator01709', oscillations=3),
 PowerFunctionGenerator(exponent_param=0.625487175284582, f0=0.622817884800272, f1=0.6687864412671407, name='PowerFunctionGenerator01710')]

In [21]:
import pandas as pd

pd.DataFrame([s.param.values() for s in sampled_utility])

sample_p_i = pn.widgets.IntSlider(name='Utility Value Function', start=0, end=len(sampled_utility)-1)

pn.Row(sample_p_i, pn.bind(lambda i: sampled_utility[i].view(), i=sample_p_i))#.param.value_throttled))

Row
    [0] IntSlider(end=89, name='Utility Value Function')
    [1] ParamFunction(function, _pane=HoloViews, defer_load=False)

## 3.1 Side Quest: Generating Value Functions - Continued

In [22]:
import param
import numpy as np
import pandas as pd
import hvplot.pandas
import panel as pn

class CurveGenerator(param.Parameterized):
    f0 = param.Number(default=0.2, bounds=(0, 1), doc="Value of f(0)")
    f1 = param.Number(default=0.8, bounds=(0, 1), doc="Value of f(1)")
    initial_slope = param.Number(default=1, bounds=(-5, 5), doc="Initial slope of the curve")
    exponent = param.Number(default=1, bounds=(1, 5), doc="Exponent of the curve")
    num_oscillations = param.Integer(default=1, bounds=(0, 5), doc="Number of oscillations/peaks in the curve")
    
    def x(self):
        return np.linspace(0, 1, 400)
    
    def f(self, x):
        epsilon = 1e-10
        b = self.f0
        a = self.initial_slope / (self.exponent * (b + epsilon)**(self.exponent-1))
        c = (self.f1 - self.f0 - a) / 2
        d = self.num_oscillations
        y = a*x**self.exponent + b + c*np.sin(d*np.pi*x)
        
        # Scale and shift the curve to ensure it starts at f0 and ends at f1
        y = self.f0 + (self.f1 - self.f0) * (y - y.min()) / (y.max() - y.min())
        return y
    
    @param.depends('f0', 'f1', 'initial_slope', 'exponent', 'num_oscillations')
    def view(self):
        x = self.x()
        y = self.f(x)
        df = pd.DataFrame({'x': x, 'y': y})
        return df.hvplot.line(x='x', y='y', ylim=(0, 1.01), width=500, height=400)

class SigmoidGenerator(param.Parameterized):
    f0 = param.Number(default=0.5, bounds=(0, 1), doc="Value of the function at x=0")
    f1 = param.Number(default=0.5, bounds=(0, 1), doc="Value of the function at x=1")
    initial_slope = param.Number(default=1, bounds=(-5, 5), doc="Initial slope of the curve")
    exponent = param.Number(default=0.3, bounds=(0.1, 0.5), doc="Exponent of the curve")
    oscillations = param.Integer(default=1, bounds=(1, 5), doc="Number of oscillations/peaks in the curve")
    
    def x(self):
        return np.linspace(0, 1, 400)
    
    def f(self, x):
        y = self.f0 + (self.f1 - self.f0) / (1 + np.exp(-self.initial_slope * (x - 0.5) * 10))**self.exponent
        y = y + 0.1 * np.sin(self.oscillations * np.pi * x)
        
        # Clip y values to ensure they stay within [0, 1]
        y = np.clip(y, 0, 1)
        return y
    
    @param.depends('f0', 'f1', 'initial_slope', 'exponent', 'oscillations')
    def view(self):
        x = self.x()
        y = self.f(x)
        df = pd.DataFrame({'x': x, 'y': y})
        return df.hvplot.line(x='x', y='y', ylim=(-0.01, 1.01))

class PowerFunctionGenerator(param.Parameterized):
    f0 = param.Number(default=0.1, bounds=(0, 1), doc="Value of the function at x=0")
    f1 = param.Number(default=0.5, bounds=(0, 1), doc="Value of the function at x=1")
    exponent_param = param.Number(default=0.5, bounds=(0.1, 2), doc="Parameter determining the exponent and slope")
    
    def x(self):
        return np.linspace(0.001, 1, 400)  # Start from 0.001 to avoid division by zero
    
    def f(self, x):
        epsilon = 1e-10
        b = 2 * self.exponent_param  # This maps [0, 1] to [0, 2] for the exponent
        a = self.f0
        c = (self.f1 - self.f0) / (1 ** b - 0 ** b + epsilon)
        y = a + c * x ** b
        
        # Clip y values to ensure they stay within [0, 1]
        y = np.clip(y, 0, 1)
        return y
    
    @param.depends('f0', 'f1', 'exponent_param')
    def view(self):
        x = self.x()
        y = self.f(x)
        df = pd.DataFrame({'x': x, 'y': y})
        return df.hvplot.line(x='x', y='y', ylim=(0, 1.01))


In [23]:
import numbergen as ng
import numpy as np


# For CurveGenerator
def polynomial_curve_generator_params():
    return dict(
        f0=ng.UniformRandom(lbound=0, ubound=0.5, seed=None)(),
        f1=ng.UniformRandom(lbound=0, ubound=1)(),
        initial_slope=ng.UniformRandom(lbound=-5, ubound=5)(),
        exponent=ng.UniformRandom(lbound=1, ubound=5)(),
        num_oscillations=int(ng.UniformRandom(lbound=0, ubound=5)())
    )

# For SigmoidGenerator
def sigmoid_curve_generator_params():
    return dict(
        f0=ng.UniformRandom(lbound=0, ubound=0.5)(),
        f1=ng.UniformRandom(lbound=0, ubound=1)(),
        initial_slope=ng.UniformRandom(lbound=-5, ubound=5)(),
        exponent=ng.UniformRandom(lbound=0.1, ubound=0.5)(),
        oscillations=int(ng.UniformRandom(lbound=1, ubound=5)())
    )

# For PowerFunctionGenerator
def power_curve_generator_params():
    return dict(
        f0=ng.UniformRandom(lbound=0, ubound=0.5)(),
        f1=ng.UniformRandom(lbound=0, ubound=1)(),
        exponent_param=ng.UniformRandom(lbound=0.1, ubound=2)()
)



# Now, you can use these dictionaries to create instances of your classes as you've done in your code.
value_function_generators = np.array([
    (CurveGenerator, polynomial_curve_generator_params),
    (SigmoidGenerator, sigmoid_curve_generator_params),
    (PowerFunctionGenerator, power_curve_generator_params),
])

# Use numpy's advanced indexing to obtain the selected_generators
value_function_samples= value_function_generators[np.random.choice(len(value_function_generators), size=len(public_goods)*len(society))]

# Instantiate utility curves using python param and numbergen
value_functions = [Generator(**params()) for Generator, params in value_function_samples]

In [24]:
df_value_functions = pd.DataFrame([s.f(s.x()) for s in value_functions]).T
df_value_functions.columns = [(p, i) for p in public_goods for i in society]
df_value_functions.columns.name = "value_p_i"
df_value_functions.index = np.linspace(0,1,len(df_value_functions))
df_value_functions.index.name = "funding"

In [25]:
df_value_functions

value_p_i  ((0, 2), 0)  ((0, 2), 1)  ((0, 2), 2)  ((0, 2), 3)  ((0, 2), 4)  \
funding                                                                      
0.000000      0.151699     0.060651     0.419891     0.433952     0.338503   
0.002506      0.150572     0.060343     0.423040     0.434619     0.340670   
0.005013      0.149481     0.060035     0.426186     0.435260     0.342841   
0.007519      0.148417     0.059727     0.429326     0.435886     0.345015   
0.010025      0.147376     0.059419     0.432456     0.436503     0.347192   
...                ...          ...          ...          ...          ...   
0.989975      0.746034     0.135675     0.283199     0.636576     0.562958   
0.992481      0.749690     0.136523     0.286311     0.637062     0.564530   
0.994987      0.753349     0.137374     0.289432     0.637549     0.566104   
0.997494      0.757013     0.138227     0.292560     0.638036     0.567678   
1.000000      0.760680     0.139083     0.295691     0.638523     0.569253   

value_p_i  ((0, 2), 5)  ((0, 2), 6)  ((0, 2), 7)  ((0, 2), 8)  ((0, 2), 9)  \
funding                                                                      
0.000000      0.449200     0.010563     0.274761     0.032778     0.095373   
0.002506      0.452349     0.011375     0.274761     0.033565     0.096957   
0.005013      0.455495     0.012187     0.274761     0.034353     0.098542   
0.007519      0.458634     0.012999     0.274762     0.035140     0.100126   
0.010025      0.461765     0.013812     0.274762     0.035927     0.101709   
...                ...          ...          ...          ...          ...   
0.989975      0.034644     0.092490     0.716784     0.341320     0.474751   
0.992481      0.037689     0.091703     0.720579     0.340542     0.476323   
0.994987      0.040747     0.090916     0.724396     0.339763     0.477897   
0.997494      0.043812     0.090129     0.728236     0.338984     0.479471   
1.000000      0.046883     0.089342     0.732100     0.338204     0.481046   

value_p_i  ...  ((2, 10), 20)  ((2, 10), 21)  ((2, 10), 22)  ((2, 10), 23)  \
funding    ...                                                               
0.000000   ...       0.589431       0.771052       0.088795       0.289102   
0.002506   ...       0.592556       0.771038       0.102061       0.289127   
0.005013   ...       0.595667       0.771006       0.110965       0.289151   
0.007519   ...       0.598765       0.770957       0.118174       0.289175   
0.010025   ...       0.601852       0.770894       0.124402       0.289199   
...        ...            ...            ...            ...            ...   
0.989975   ...       0.269194       0.208977       0.578287       0.283284   
0.992481   ...       0.270983       0.206441       0.578940       0.283208   
0.994987   ...       0.272772       0.203900       0.579592       0.283131   
0.997494   ...       0.274560       0.201354       0.580243       0.283054   
1.000000   ...       0.276346       0.198803       0.580894       0.282977   

value_p_i  ((2, 10), 24)  ((2, 10), 25)  ((2, 10), 26)  ((2, 10), 27)  \
funding                                                                 
0.000000        0.133788       0.228345       0.218922       0.227307   
0.002506        0.133788       0.229984       0.219298       0.224544   
0.005013        0.133788       0.231622       0.219673       0.221784   
0.007519        0.133788       0.233256       0.220049       0.219031   
0.010025        0.133788       0.234885       0.220425       0.216286   
...                  ...            ...            ...            ...   
0.989975        0.518905       0.121271       0.128251       0.414417   
0.992481        0.522637       0.122037       0.127267       0.412685   
0.994987        0.526395       0.122802       0.126280       0.410948   
0.997494        0.530179       0.123566       0.125291       0.409209   
1.000000        0.533991       0.124325       0.124299       0.407471   

value

In [26]:
df_value_functions.hvplot.line(x='funding', color='blue', alpha=0.2, line_width=5)

:NdOverlay   [value_p_i]
   :Curve   [funding]   (value)

In [27]:
 df_value_functions.melt(ignore_index=False)

value_p_i     value
funding                          
0.000000    ((0, 2), 0)  0.151699
0.002506    ((0, 2), 0)  0.150572
0.005013    ((0, 2), 0)  0.149481
0.007519    ((0, 2), 0)  0.148417
0.010025    ((0, 2), 0)  0.147376
...                 ...       ...
0.989975  ((2, 10), 29)  0.842244
0.992481  ((2, 10), 29)  0.841457
0.994987  ((2, 10), 29)  0.840670
0.997494  ((2, 10), 29)  0.839883
1.000000  ((2, 10), 29)  0.839095

[36000 rows x 2 columns]

In [28]:
df_value_functions_melted = df_value_functions.melt(ignore_index=False)
df_value_functions_melted

value_p_i     value
funding                          
0.000000    ((0, 2), 0)  0.151699
0.002506    ((0, 2), 0)  0.150572
0.005013    ((0, 2), 0)  0.149481
0.007519    ((0, 2), 0)  0.148417
0.010025    ((0, 2), 0)  0.147376
...                 ...       ...
0.989975  ((2, 10), 29)  0.842244
0.992481  ((2, 10), 29)  0.841457
0.994987  ((2, 10), 29)  0.840670
0.997494  ((2, 10), 29)  0.839883
1.000000  ((2, 10), 29)  0.839095

[36000 rows x 2 columns]

In [29]:
df_value_functions_melted['public_good'] = df_value_functions_melted['value_p_i'].astype(str).apply(eval).apply(lambda x: x[0]).astype(str)
df_value_functions_melted['citizen'] = df_value_functions_melted['value_p_i'].astype(str).apply(eval).apply(lambda x: x[1]).astype(str)

In [30]:
df_value_functions_melted

value_p_i     value public_good citizen
funding                                              
0.000000    ((0, 2), 0)  0.151699      (0, 2)       0
0.002506    ((0, 2), 0)  0.150572      (0, 2)       0
0.005013    ((0, 2), 0)  0.149481      (0, 2)       0
0.007519    ((0, 2), 0)  0.148417      (0, 2)       0
0.010025    ((0, 2), 0)  0.147376      (0, 2)       0
...                 ...       ...         ...     ...
0.989975  ((2, 10), 29)  0.842244     (2, 10)      29
0.992481  ((2, 10), 29)  0.841457     (2, 10)      29
0.994987  ((2, 10), 29)  0.840670     (2, 10)      29
0.997494  ((2, 10), 29)  0.839883     (2, 10)      29
1.000000  ((2, 10), 29)  0.839095     (2, 10)      29

[36000 rows x 4 columns]

In [31]:
import hvplot.pandas

In [32]:
df_value_functions_melted.hvplot.scatter(y='value', by='public_good', alpha=0.1)

:NdOverlay   [public_good]
   :Scatter   [funding]   (value)

In [33]:
mean_utility_df = df_value_functions_melted.groupby(['funding', 'public_good'])[['value']].mean().reset_index()

In [34]:
mean_utility_df.hvplot.scatter(y='value', by='public_good')

:NdOverlay   [public_good]
   :Scatter   [index]   (value)

In [35]:
mean_utility_df

funding public_good     value
0     0.000000      (0, 2)  0.300212
1     0.000000      (1, 3)  0.366828
2     0.000000     (2, 10)  0.342331
3     0.002506      (0, 2)  0.300669
4     0.002506      (1, 3)  0.367554
...        ...         ...       ...
1195  0.997494      (1, 3)  0.461223
1196  0.997494     (2, 10)  0.401987
1197  1.000000      (0, 2)  0.453340
1198  1.000000      (1, 3)  0.461156
1199  1.000000     (2, 10)  0.402271

[1200 rows x 3 columns]

In [36]:
df_value_functions

value_p_i  ((0, 2), 0)  ((0, 2), 1)  ((0, 2), 2)  ((0, 2), 3)  ((0, 2), 4)  \
funding                                                                      
0.000000      0.151699     0.060651     0.419891     0.433952     0.338503   
0.002506      0.150572     0.060343     0.423040     0.434619     0.340670   
0.005013      0.149481     0.060035     0.426186     0.435260     0.342841   
0.007519      0.148417     0.059727     0.429326     0.435886     0.345015   
0.010025      0.147376     0.059419     0.432456     0.436503     0.347192   
...                ...          ...          ...          ...          ...   
0.989975      0.746034     0.135675     0.283199     0.636576     0.562958   
0.992481      0.749690     0.136523     0.286311     0.637062     0.564530   
0.994987      0.753349     0.137374     0.289432     0.637549     0.566104   
0.997494      0.757013     0.138227     0.292560     0.638036     0.567678   
1.000000      0.760680     0.139083     0.295691     0.638523     0.569253   

value_p_i  ((0, 2), 5)  ((0, 2), 6)  ((0, 2), 7)  ((0, 2), 8)  ((0, 2), 9)  \
funding                                                                      
0.000000      0.449200     0.010563     0.274761     0.032778     0.095373   
0.002506      0.452349     0.011375     0.274761     0.033565     0.096957   
0.005013      0.455495     0.012187     0.274761     0.034353     0.098542   
0.007519      0.458634     0.012999     0.274762     0.035140     0.100126   
0.010025      0.461765     0.013812     0.274762     0.035927     0.101709   
...                ...          ...          ...          ...          ...   
0.989975      0.034644     0.092490     0.716784     0.341320     0.474751   
0.992481      0.037689     0.091703     0.720579     0.340542     0.476323   
0.994987      0.040747     0.090916     0.724396     0.339763     0.477897   
0.997494      0.043812     0.090129     0.728236     0.338984     0.479471   
1.000000      0.046883     0.089342     0.732100     0.338204     0.481046   

value_p_i  ...  ((2, 10), 20)  ((2, 10), 21)  ((2, 10), 22)  ((2, 10), 23)  \
funding    ...                                                               
0.000000   ...       0.589431       0.771052       0.088795       0.289102   
0.002506   ...       0.592556       0.771038       0.102061       0.289127   
0.005013   ...       0.595667       0.771006       0.110965       0.289151   
0.007519   ...       0.598765       0.770957       0.118174       0.289175   
0.010025   ...       0.601852       0.770894       0.124402       0.289199   
...        ...            ...            ...            ...            ...   
0.989975   ...       0.269194       0.208977       0.578287       0.283284   
0.992481   ...       0.270983       0.206441       0.578940       0.283208   
0.994987   ...       0.272772       0.203900       0.579592       0.283131   
0.997494   ...       0.274560       0.201354       0.580243       0.283054   
1.000000   ...       0.276346       0.198803       0.580894       0.282977   

value_p_i  ((2, 10), 24)  ((2, 10), 25)  ((2, 10), 26)  ((2, 10), 27)  \
funding                                                                 
0.000000        0.133788       0.228345       0.218922       0.227307   
0.002506        0.133788       0.229984       0.219298       0.224544   
0.005013        0.133788       0.231622       0.219673       0.221784   
0.007519        0.133788       0.233256       0.220049       0.219031   
0.010025        0.133788       0.234885       0.220425       0.216286   
...                  ...            ...            ...            ...   
0.989975        0.518905       0.121271       0.128251       0.414417   
0.992481        0.522637       0.122037       0.127267       0.412685   
0.994987        0.526395       0.122802       0.126280       0.410948   
0.997494        0.530179       0.123566       0.125291       0.409209   
1.000000        0.533991       0.124325       0.124299       0.407471   

value

In [37]:
import param
import numpy as np
import panel as pn
import hvplot.pandas
import pandas as pd

class ConcaveFunctionGenerator(param.Parameterized):
    f0 = param.Number(default=0.2, bounds=(0, 1), doc="Value of f(0)")
    f1 = param.Number(default=0.8, bounds=(0, 1), doc="Value of f(1)")
    slope = param.Number(default=10, bounds=(1, 50), doc="Slope of the curve")

    @param.depends('f0', 'f1', 'slope')
    def f(self, x):
        # Using the sigmoid function as a base
        y = 1 / (1 + np.exp(-self.slope * (x - 0.5)))
        
        # Adjusting the function to start at f0 and end at f1
        y = self.f0 + (self.f1 - self.f0) * (y - y.min()) / (y.max() - y.min())
        
        return y

    @param.depends('f0', 'f1', 'slope')
    def view(self):
        x = np.linspace(0, 1, 400)
        y = self.f(x)
        df = pd.DataFrame({'x': x, 'y': y})
        return df.hvplot.line(x='x', y='y', ylim=(0, 1.01), width=500, height=400)

concave_gen = ConcaveFunctionGenerator()
pn.Row(concave_gen.param, concave_gen.view).servable()


Row
    [0] Column(margin=(5, 10), name='ConcaveFunctionGenerator'...)
        [0] StaticText(value='<b>ConcaveFunctionGenerat...)
        [1] FloatSlider(name='F0', value=0.2)
        [2] FloatSlider(name='F1', value=0.8)
        [3] FloatSlider(end=50, name='Slope', start=1, value=10)
    [1] ParamMethod(method, _pane=HoloViews, defer_load=False)

In [38]:
import param
import numpy as np
import panel as pn
import hvplot.pandas
import pandas as pd

class ConcaveFunctionGenerator(param.Parameterized):
    f0 = param.Number(default=0.2, bounds=(0, 1), doc="Value of f(0)")
    f1 = param.Number(default=0.8, bounds=(0, 1), doc="Value of f(1)")
    steepness = param.Number(default=5, bounds=(1, 20), doc="Steepness of the curve")

    @param.depends('f0', 'f1', 'steepness')
    def f(self, x):
        # Using the negative exponential function as a base
        y = 1 - np.exp(-self.steepness * x)
        
        # Adjusting the function to start at f0 and end at f1
        y = self.f0 + (self.f1 - self.f0) * (y - y.min()) / (y.max() - y.min())
        
        return y

    @param.depends('f0', 'f1', 'steepness')
    def view(self):
        x = np.linspace(0, 1, 400)
        y = self.f(x)
        df = pd.DataFrame({'x': x, 'y': y})
        return df.hvplot.line(x='x', y='y', ylim=(0, 1.01), width=500, height=400)

concave_gen = ConcaveFunctionGenerator()
pn.Row(concave_gen.param, concave_gen.view).servable()


Row
    [0] Column(margin=(5, 10), name='ConcaveFunctionGenerator'...)
        [0] StaticText(value='<b>ConcaveFunctionGenerat...)
        [1] FloatSlider(name='F0', value=0.2)
        [2] FloatSlider(name='F1', value=0.8)
        [3] FloatSlider(end=20, name='Steepness', start=1, value=5)
    [1] ParamMethod(method, _pane=HoloViews, defer_load=False)

In [39]:
import param
import numpy as np
import panel as pn
import hvplot.pandas
import pandas as pd

class ConcaveFunctionGenerator(param.Parameterized):
    f0 = param.Number(default=0.2, bounds=(0, 1), doc="Value of f(0)")
    f1 = param.Number(default=0.8, bounds=(0, 1), softbounds=(0, 1), doc="Value of f(1)")
    steepness = param.Number(default=5, bounds=(1, 20), doc="Steepness of the curve")

    def __init__(self, **params):
        super().__init__(**params)
        self._update_f1_bounds()

    @param.depends('f0', watch=True)
    def _update_f1_bounds(self):
        # Clip the value of f1 if it's below f0
        self.f1 = max(self.f0, self.f1)
        
        # Update the lower bound of f1 to be the value of f0
        self.param['f1'].bounds = (self.f0, 1)
        
    def x(self):
        return np.linspace(0, 1, 400)

    @param.depends('f0', 'f1', 'steepness')
    def f(self, x):
        # Using the negative exponential function as a base
        y = 1 - np.exp(-self.steepness * x)
        
        # Adjusting the function to start at f0 and end at f1
        y = self.f0 + (self.f1 - self.f0) * (y - y.min()) / (y.max() - y.min())
        
        return y

    @param.depends('f0', 'f1', 'steepness')
    def view(self):
        x = self.x()
        y = self.f(x)
        df = pd.DataFrame({'x': x, 'y': y})
        return df.hvplot.line(x='x', y='y', ylim=(0, 1.01))

concave_gen = ConcaveFunctionGenerator()
pn.Row(concave_gen.param, concave_gen.view).servable()


Row
    [0] Column(margin=(5, 10), name='ConcaveFunctionGenerator'...)
        [0] StaticText(value='<b>ConcaveFunctionGenerat...)
        [1] FloatSlider(name='F0', value=0.2)
        [2] FloatSlider(name='F1', start=0.2, value=0.8)
        [3] FloatSlider(end=20, name='Steepness', start=1, value=5)
    [1] ParamMethod(method, _pane=HoloViews, defer_load=False)

In [40]:
ConcaveFunctionGenerator(f0=1,f1=0)

ConcaveFunctionGenerator(f0=1, f1=1, name='ConcaveFunctionGenerator07123', steepness=5)

In [41]:
import numbergen as ng
import numpy as np


# For CurveGenerator
def concave_function_generator():
    return dict(
        f0=ng.BoundedNumber(generator=ng.NormalRandom(mu=0.1, sigma=0.2), bounds=(0,1))(),
        f1=ng.BoundedNumber(generator=ng.NormalRandom(mu=0.5, sigma=0.3), bounds=(0,1))(),
        steepness=ng.UniformRandom(lbound=1, ubound=20)(),
    )

In [42]:
concave_function_generator()

{'f0': 0.26977499037785957,
 'f1': 0.2370247258594576,
 'steepness': 6.355138199782189}

In [43]:
value_functions = [ConcaveFunctionGenerator(**concave_function_generator()) for p_i in range(len(public_goods)*len(society))]

In [44]:
df_value_functions = pd.DataFrame([s.f(s.x()) for s in value_functions]).T
df_value_functions.columns = [(p, i) for p in public_goods for i in society]
df_value_functions.columns.name = "value_p_i"
df_value_functions.index = np.linspace(0,1,len(df_value_functions))
df_value_functions.index.name = "funding"

In [45]:
df_value_functions

value_p_i  ((0, 2), 0)  ((0, 2), 1)  ((0, 2), 2)  ((0, 2), 3)  ((0, 2), 4)  \
funding                                                                      
0.000000      0.000000     0.324186     0.042379     0.017272     0.117196   
0.002506      0.015168     0.330159     0.048926     0.022200     0.130418   
0.005013      0.029959     0.336070     0.055331     0.027077     0.143367   
0.007519      0.044384     0.341919     0.061597     0.031902     0.156049   
0.010025      0.058451     0.347707     0.067725     0.036677     0.168469   
...                ...          ...          ...          ...          ...   
0.989975      0.611733     0.885284     0.342846     0.480066     0.757676   
0.992481      0.611733     0.885377     0.342847     0.480143     0.757680   
0.994987      0.611734     0.885469     0.342848     0.480218     0.757683   
0.997494      0.611735     0.885560     0.342849     0.480294     0.757686   
1.000000      0.611736     0.885650     0.342850     0.480368     0.757690   

value_p_i  ((0, 2), 5)  ((0, 2), 6)  ((0, 2), 7)  ((0, 2), 8)  ((0, 2), 9)  \
funding                                                                      
0.000000      0.290811     0.574600     0.127617     0.303204     0.000000   
0.002506      0.293011     0.574948     0.135549     0.307953     0.005096   
0.005013      0.295202     0.575291     0.143370     0.312533     0.010160   
0.007519      0.297384     0.575629     0.151081     0.316948     0.015191   
0.010025      0.299558     0.575962     0.158683     0.321205     0.020191   
...                ...          ...          ...          ...          ...   
0.989975      0.718231     0.598939     0.689497     0.435718     0.739538   
0.992481      0.718656     0.598940     0.689527     0.435718     0.739953   
0.994987      0.719079     0.598941     0.689556     0.435718     0.740366   
0.997494      0.719501     0.598942     0.689585     0.435718     0.740775   
1.000000      0.719920     0.598943     0.689613     0.435718     0.741182   

value_p_i  ...  ((2, 10), 20)  ((2, 10), 21)  ((2, 10), 22)  ((2, 10), 23)  \
funding    ...                                                               
0.000000   ...       0.323616       0.119673       0.255195       0.000000   
0.002506   ...       0.323616       0.128576       0.256101       0.014083   
0.005013   ...       0.323616       0.137361       0.256994       0.027534   
0.007519   ...       0.323616       0.146028       0.257875       0.040382   
0.010025   ...       0.323616       0.154578       0.258742       0.052654   
...        ...            ...            ...            ...            ...   
0.989975   ...       0.323616       0.780425       0.318334       0.314003   
0.992481   ...       0.323616       0.780468       0.318337       0.314003   
0.994987   ...       0.323616       0.780510       0.318340       0.314003   
0.997494   ...       0.323616       0.780552       0.318343       0.314003   
1.000000   ...       0.323616       0.780593       0.318346       0.314003   

value_p_i  ((2, 10), 24)  ((2, 10), 25)  ((2, 10), 26)  ((2, 10), 27)  \
funding                                                                 
0.000000        0.000000       0.000000       0.063273       0.043527   
0.002506        0.047478       0.009234       0.066885       0.049880   
0.005013        0.092658       0.018338       0.070473       0.056194   
0.007519        0.135649       0.027313       0.074037       0.062469   
0.010025        0.176559       0.036162       0.077578       0.068706   
...                  ...            ...            ...            ...   
0.989975        0.980511       0.651978       0.572333       0.988614   
0.992481        0.980511       0.652011       0.572600       0.989175   
0.994987        0.980511       0.652044       0.572865       0.989731   
0.997494        0.980511       0.652077       0.573129       0.990284   
1.000000        0.980511       0.652109       0.573391       0.990834   

value

In [46]:
import pandas as pd

pd.DataFrame([s.param.values() for s in value_functions])

sample_p_i = pn.widgets.IntSlider(name='Utility Value Function', start=0, end=len(value_functions)-1)

pn.Row(sample_p_i, pn.bind(lambda i: value_functions[i].view(), i=sample_p_i))#.param.value_throttled))

Row
    [0] IntSlider(end=89, name='Utility Value Function')
    [1] ParamFunction(function, _pane=HoloViews, defer_load=False)

In [47]:
df_value_functions.hvplot.line(x='funding', color='blue', alpha=0.1, line_width=3)

:NdOverlay   [value_p_i]
   :Curve   [funding]   (value)

In [48]:
df_value_functions['mean'] = df_value_functions.mean(axis=1)
df_value_functions['std'] = df_value_functions.std(axis=1)
df_value_functions['low'] = df_value_functions['mean'] - df_value_functions['std']
df_value_functions['high'] = df_value_functions['mean'] + df_value_functions['std']

In [49]:
df_value_functions.hvplot.line(y='mean', ylabel='Value to Society') * df_value_functions.hvplot.area(y='low',y2='high', alpha=0.5)

:Overlay
   .Curve.I :Curve   [funding]   (mean)
   .Area.I  :Area   [funding]   (low,high)

## Public Goods Distributions Explorer

This widget allows us to sample funding distributions F_P. We can explore F_P as a normal, constant, uniform, or exponential distribution.

In [201]:
public_goods_funding_model = {'constant_value': 0.5,
 'distribution_type': 'exponential',
 'lambda_param': 2.8000000000000003,
 'mean': 0.2,
 'n': len(public_goods),
 'name': 'PublicGoodsFundingDistributionGenerator53483',
 'std_dev': 0.2}

In [202]:
import param
import numpy as np
import pandas as pd
import panel as pn
import hvplot.pandas

class PublicGoodsFundingDistributionGenerator(param.Parameterized):
    distribution_type = param.ObjectSelector(default="normal", objects=["normal", "constant", "uniform", "exponential"])
    mean = param.Number(default=0.5, bounds=(0, 1))
    n = param.Integer(default=100, bounds=(1, 1000))
    
    # Additional parameters for specific distributions
    std_dev = param.Number(default=0.1, bounds=(0, 0.5))  # for normal distribution
    constant_value = param.Number(default=0.5, bounds=(0, 1))  # for constant distribution
    lambda_param = param.Number(default=1.0, bounds=(0.1, 5))  # for exponential distribution
    
    @param.depends('distribution_type', 'mean', 'n', 'std_dev', 'constant_value', 'lambda_param')
    def generate_distribution(self):
        if self.distribution_type == "normal":
            distribution = np.clip(np.random.normal(self.mean, self.std_dev, self.n), 0, 1)
        elif self.distribution_type == "constant":
            distribution = np.full(self.n, self.constant_value)
        elif self.distribution_type == "uniform":
            distribution = np.random.uniform(0, 1, self.n)
        elif self.distribution_type == "exponential":
            distribution = np.clip(np.random.exponential(1/self.lambda_param, self.n), 0, 1)
        distribution = pd.Series(distribution, name='Public Goods Funding Distribution')
        return distribution / distribution.sum()
        
    
    @param.depends('distribution_type', 'mean', 'n', 'std_dev', 'constant_value', 'lambda_param')
    def view(self):
        data = self.generate_distribution()
        df = pd.DataFrame({'Value': data})
        return df.hvplot.hist('Value', bins=30, title='Public Goods Funding Histogram')

# Create an instance
dist_gen = PublicGoodsFundingDistributionGenerator(**public_goods_funding_model)

# Use panel to render the interactive system
pn.Row(dist_gen.param, dist_gen.view).servable()


Row
    [0] Column(margin=(5, 10), name='PublicGoodsFundingDistrib...)
        [0] StaticText(value='<b>PublicGoodsFundingDist...)
        [1] Select(name='Distribution type', options=OrderedDict([('normal', ...]), value='exponential')
        [2] FloatSlider(name='Mean', value=0.2)
        [3] IntSlider(end=1000, name='N', start=1, value=2)
        [4] FloatSlider(end=0.5, name='Std dev', value=0.2)
        [5] FloatSlider(name='Constant value', value=0.5)
        [6] FloatSlider(end=5, name='Lambda param', start=0.1, value=2.8000000000000003)
    [1] ParamMethod(method, _pane=HoloViews, defer_load=False)

#### Saving State with Params

In [160]:
dist_gen.param.values()

{'constant_value': 0.5,
 'distribution_type': 'exponential',
 'lambda_param': 2.8000000000000003,
 'mean': 0.2,
 'n': 20,
 'name': 'PublicGoodsFundingDistributionGenerator53483',
 'std_dev': 0.2}

In [161]:
dist_gen.generate_distribution()

0     0.069856
1     0.074165
2     0.035582
3     0.119106
4     0.007148
5     0.079765
6     0.015976
7     0.002180
8     0.040688
9     0.071838
10    0.001175
11    0.047208
12    0.102436
13    0.031604
14    0.034950
15    0.007421
16    0.010495
17    0.038500
18    0.030990
19    0.178916
Name: Public Goods Funding Distribution, dtype: float64